In [1]:
#bibliotecas
#!pip install pandas numpy

import pandas as pd
import numpy as np
import os

In [2]:
# Carregar o DataFrame e pega a estacao mais proxima

dados_df =  pd.read_csv("leitura.csv",  sep=';', decimal=',', parse_dates=['DATA'], dayfirst=True)
dados_df.head(2)

CODIGO       DATA  VALOR
0  1742017 1980-01-01    1.6
1  1742017 1980-01-02   10.6

In [3]:


# Converter mapeamento para DataFrame
estacao_df =  pd.read_csv("estacao_mais_proxima.csv", encoding='utf-8', sep=';', decimal=',')
estacao_df.head(2)


CODIGO   LATITUDE  LONGITUDE         NOME               1proxima  \
0  1742017 -17.845600 -42.075600  MALACACHETA               ÁGUA BOA   
1  1742019 -17.992201 -42.393902     ÁGUA BOA  SANTA MARIA DO SUAÇUÍ   

                2proxima              3proxima  1codigo  2codigo  3codigo  
0  SANTA MARIA DO SUAÇUÍ  SÃO JOÃO EVANGELISTA  1742019  1842008  1842020  
1            MALACACHETA  SÃO JOÃO EVANGELISTA  1842008  1742017  1842020

In [4]:
# Copiar dados_df para uma variável para atualização
AtualizaDados = dados_df.copy()

# Caminho do arquivo de log no diretório atual
log_file_path = os.path.join(os.getcwd(), 'atualizacao_dados.txt')

# Abrir o arquivo de log para escrita
with open(log_file_path, 'w') as log_file:
    # Iterar sobre AtualizaDados para atualizar os valores
    for index, row in AtualizaDados.iterrows():
        valor = row['VALOR']
        data = row['DATA']
        if valor <= -1:
            log_file.write(f"Código: {row['CODIGO']}, Data: {row['DATA']}, Valor: {valor}\n")

            codigo_filtrado = row['CODIGO']
            linhas_filtradas = estacao_df.loc[estacao_df['CODIGO'] == codigo_filtrado]
            
            # Iterar sobre os códigos próximos (1codigo, 2codigo, 3codigo)
            for i in range(1, 4):  # Considerando as três primeiras colunas de códigos
                codigo_proximo = linhas_filtradas[f'{i}codigo'].iloc[0]
                filtro = (dados_df['CODIGO'] == codigo_proximo) & (dados_df['DATA'] == data)
                valor_proximo = dados_df.loc[filtro, 'VALOR'].values
                
                log_file.write(f"{i}codigo: {codigo_proximo} Valor: {valor_proximo}\n")
                
                # Verificar se o valor encontrado não é menor ou igual a -1
                if len(valor_proximo) > 0 and valor_proximo[0] > -1:
                    AtualizaDados.loc[index, 'VALOR'] = valor_proximo[0]

                    log_file.write(f"Valor atual {row['VALOR']} - Valor atualizado para: {valor_proximo[0]}\n")
                    break  # Parar o loop se encontrar um valor válido
            
            log_file.write("---------------------------------------------------\n")

# Exibir mensagem após completar o processo
print("Dados atualizados:")
AtualizaDados.to_csv("dados_atualizados_mais_proximo.csv", sep=";", encoding='utf-8', decimal=',', index=False)
#print(AtualizaDados)

Dados atualizados:
